# Limpieza del dataframe amazon_prime_titles.csv
## Junio 2025
## by Francis

### Importar funciones generales

In [1]:
import sys
sys.path.append(r"C:\Users\FRANCIS\Documents\Proyecto_Streaming\scripts") 
import utils
import pandas as pd

### Carga del DataFrame

In [2]:
df_amazon = utils.cargar_datos(r"C:\Users\FRANCIS\Documents\Proyecto_Streaming\data\amazon_prime_titles.csv")

### Inspección del DataFrame

In [3]:
df_amazon.head()

show_id   type                 title        director  \
0      s1  Movie   The Grand Seduction    Don McKellar   
1      s2  Movie  Take Care Good Night    Girish Joshi   
2      s3  Movie  Secrets of Deception     Josh Webber   
3      s4  Movie    Pink: Staying True  Sonia Anderson   
4      s5  Movie         Monster Maker    Giles Foster   

                                                cast         country  \
0     Brendan Gleeson, Taylor Kitsch, Gordon Pinsent          Canada   
1   Mahesh Manjrekar, Abhay Mahajan, Sachin Khedekar           India   
2  Tom Sizemore, Lorenzo Lamas, Robert LaSardo, R...   United States   
3  Interviews with: Pink, Adele, Beyoncé, Britney...   United States   
4  Harry Dean Stanton, Kieran O'Brien, George Cos...  United Kingdom   

       date_added  release_year rating duration                listed_in  \
0  March 30, 2021          2014    NaN  113 min            Comedy, Drama   
1  March 30, 2021          2018    13+  110 min     Drama, International   
2  March 30, 2021          2017    NaN   74 min  Action, Drama, Suspense   
3  March 30, 2021          2014    NaN   69 min              Documentary   
4  March 30, 2021          1989    NaN   45 min           Drama, Fantasy   

                                         description  
0  A small fishing village must procure a local d...  
1  A Metro Family decides to fight a Cyber Crimin...  
2  After a man discovers his wife is cheating on ...  
3  Pink breaks the mold once again, bringing her ...  
4  Teenage Matt Banting wants to work with a famo...

In [4]:
df_amazon.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9668 entries, 0 to 9667
Data columns (total 12 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   show_id       9668 non-null   object
 1   type          9668 non-null   object
 2   title         9668 non-null   object
 3   director      7585 non-null   object
 4   cast          8435 non-null   object
 5   country       672 non-null    object
 6   date_added    155 non-null    object
 7   release_year  9668 non-null   int64 
 8   rating        9331 non-null   object
 9   duration      9668 non-null   object
 10  listed_in     9668 non-null   object
 11  description   9668 non-null   object
dtypes: int64(1), object(11)
memory usage: 906.5+ KB


### Convertir columna con fechas a datetime 

In [5]:
df_amazon = utils.convertir_a_fecha(df_amazon, ['date_added'])

In [6]:
df_amazon.dtypes

show_id                 object
type                    object
title                   object
director                object
cast                    object
country                 object
date_added      datetime64[ns]
release_year             int64
rating                  object
duration                object
listed_in               object
description             object
dtype: object

### Ver porcentaje de valores nulos

In [7]:
utils.resumen_nulos(df_amazon)

cantidad_nulos  porcentaje_nulos
date_added              9513         98.396773
country                 8996         93.049235
director                2083         21.545304
cast                    1233         12.753413
rating                   337          3.485726
show_id                    0          0.000000
type                       0          0.000000
title                      0          0.000000
release_year               0          0.000000
duration                   0          0.000000
listed_in                  0          0.000000
description                0          0.000000

### Evaluamos en las columnas que no son importantes para los objetivos de los análisis y que tienen valores nulos 

In [8]:
evaluar_director = utils.evaluar_fila(df_amazon, "director", ["date_added", "rating", "show_id","listed_in", "country", "type"])
evaluar_director.to_string()  #sí hay suficientes nulos para eliminar filas (70%< es not null)

'     show_id     type                                                                                                          title director                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          

In [9]:
df_amazon = df_amazon.drop(evaluar_director.index)

In [10]:
evaluar_cast = utils.evaluar_fila(df_amazon, "cast", ["date_added", "rating", "show_id","listed_in", "country", "type"])
evaluar_cast.to_string() #sí hay suficientes nulos para eliminar filas (70%< es not null)

'     show_id   type                                                                                           title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [11]:
df_amazon= df_amazon.drop(evaluar_cast.index)

### Reemplazamos en todas las columnas object del DataFrame los datos nulos por "Desconocido"

In [12]:
columnas_object = ["country", "director", "cast", "rating"]
df_amazon[columnas_object]= df_amazon[columnas_object].fillna("Desconocido")

### Se convierte date_added a int para poder calcular la moda y mediana dentro de sus datos

In [13]:
df_amazon["date_added"] = df_amazon["date_added"].astype("int64")

In [14]:
df_amazon.dtypes

show_id         object
type            object
title           object
director        object
cast            object
country         object
date_added       int64
release_year     int64
rating          object
duration        object
listed_in       object
description     object
dtype: object

### Se aplica la función que reemplaza los valores nulos en date_added por la mediana o moda de la agrupación de datos 

In [ ]:
df_amazon = utils.elegir_imputacion(df_amazon, columna="date_added", agrupacion=["listed_in", "type", "country"], umbral_dispersion=60)

### Se verifica si hay valores extraños o valores nulos después del reemplazo

In [ ]:
print(df_amazon["date_added"].unique())
print(df_amazon["date_added"].isnull().sum())

### Los valores están en formato int con nanosegundos: se hace la conversión a segundos con timestamp para convertir a datetime

In [16]:
# Filtrar valores extremos antes de la conversión
df_amazon = df_amazon[df_amazon["date_added"] // 10**9 > 0]  
df_amazon = df_amazon[df_amazon["date_added"] // 10**9 < 1893456000]  

df_amazon["date_added"] = pd.to_datetime(df_amazon["date_added"] // 10**9, unit="s", errors="coerce")


### Se verifica aleatoriamente los datos, se confirma si hay valores nulos todavía y si la conversión a datetime fue realizada

In [17]:
print(df_amazon[["date_added"]].sample(10))  
print(df_amazon["date_added"].isnull().sum())  
print(df_amazon.dtypes)  


     date_added
5460 2021-05-29
6025 2021-06-23
5379 2021-05-24
9362 2021-10-03
9511 2021-10-07
6051 2021-06-24
8578 2021-09-15
6782 2021-07-24
8739 2021-09-18
13   2021-04-24
0
show_id                 object
type                    object
title                   object
director                object
cast                    object
country                 object
date_added      datetime64[ns]
release_year             int64
rating                  object
duration                object
listed_in               object
description             object
dtype: object


### Se crean las columnas derivadas de date_added y se convierten a tipo int

In [18]:
df_amazon["month_added"] = df_amazon["date_added"].dt.month.astype("Int64")  
df_amazon["year_added"] = df_amazon["date_added"].dt.year.astype("Int64")

In [19]:
print(df_amazon["date_added"].isnull().sum())  
print(df_amazon[["date_added", "month_added", "year_added"]].sample(10)) 

0
     date_added  month_added  year_added
8890 2021-09-26            9        2021
7790 2021-08-26            8        2021
4783 2021-05-01            5        2021
4724 2021-04-30            4        2021
8761 2021-09-19            9        2021
8903 2021-09-26            9        2021
5004 2021-05-11            5        2021
7512 2021-08-18            8        2021
4490 2021-04-20            4        2021
7470 2021-08-16            8        2021


In [ ]:
print(df_amazon["date_added"].unique())

In [21]:
utils.resumen_nulos(df_amazon)

cantidad_nulos  porcentaje_nulos
show_id                    0               0.0
type                       0               0.0
title                      0               0.0
director                   0               0.0
cast                       0               0.0
country                    0               0.0
date_added                 0               0.0
release_year               0               0.0
rating                     0               0.0
duration                   0               0.0
listed_in                  0               0.0
description                0               0.0
month_added                0               0.0
year_added                 0               0.0

### Datos duplicados

In [22]:
df_amazon.duplicated().sum() #No hay datos duplicados

0

### Estandarizar los datos según la columna

In [23]:
df_amazon = utils.limpiar_texto(df_amazon, ["type", "country", "rating", "listed_in","title", "director", "cast","duration", "description"], conservar_mayusculas=["title", "director", "cast","duration", "description"]) 

In [24]:
df_amazon.head()

show_id   type                 title        director  \
0      s1  movie   The Grand Seduction    Don McKellar   
1      s2  movie  Take Care Good Night    Girish Joshi   
2      s3  movie  Secrets of Deception     Josh Webber   
3      s4  movie    Pink: Staying True  Sonia Anderson   
4      s5  movie         Monster Maker    Giles Foster   

                                                cast         country  \
0     Brendan Gleeson, Taylor Kitsch, Gordon Pinsent          canada   
1   Mahesh Manjrekar, Abhay Mahajan, Sachin Khedekar           india   
2  Tom Sizemore, Lorenzo Lamas, Robert LaSardo, R...   united states   
3  Interviews with: Pink, Adele, Beyoncé, Britney...   united states   
4  Harry Dean Stanton, Kieran O'Brien, George Cos...  united kingdom   

  date_added  release_year       rating duration                listed_in  \
0 2021-03-30          2014  desconocido  113 min            comedy, drama   
1 2021-03-30          2018          13+  110 min     drama, international   
2 2021-03-30          2017  desconocido   74 min  action, drama, suspense   
3 2021-03-30          2014  desconocido   69 min              documentary   
4 2021-03-30          1989  desconocido   45 min           drama, fantasy   

                                         description  month_added  year_added  
0  A small fishing village must procure a local d...            3        2021  
1  A Metro Family decides to fight a Cyber Crimin...            3        2021  
2  After a man discovers his wife is cheating on ...            3        2021  
3  Pink breaks the mold once again, bringing her ...            3        2021  
4  Teenage Matt Banting wants to work with a famo...            3        2021

In [25]:
df_amazon.dtypes

show_id                 object
type                    object
title                   object
director                object
cast                    object
country                 object
date_added      datetime64[ns]
release_year             int64
rating                  object
duration                object
listed_in               object
description             object
month_added              Int64
year_added               Int64
dtype: object

### Guardar el DataFrame limpio

In [26]:
df_amazon.to_csv("amazon_limpio.csv", index= False)
df_amazon.to_parquet("amazon_limpio.parquet")